In [1]:
from tensorflow import keras
import numpy as np
import matplotlib.pyplot as plt

In [2]:
import pandas as pd
import os
df = pd.read_csv('dataset_train.csv',sep=';')
def dfdel(value):
    return len(eval(value))
print(len(df))
df = df[df['Data_2'].map(dfdel)!=0]
df = df[df['Data_2'].map(dfdel)==240]

31383


In [3]:
class0 = df[df['Class_label']==0]
class1 = df[df['Class_label']==1]
class2 = df[df['Class_label']==2]
count = [len(class0),len(class1),len(class2)]
min(count)

6385

In [4]:
def make_model(input_shape):
    input_layer = keras.layers.Input(input_shape)

    conv1 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(input_layer)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.ReLU()(conv1)

    conv2 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(conv1)
    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.ReLU()(conv2)

    conv3 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(conv2)
    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.ReLU()(conv3)

    gap = keras.layers.GlobalAveragePooling1D()(conv3)

    output_layer = keras.layers.Dense(num_classes, activation="softmax")(gap)

    return keras.models.Model(inputs=input_layer, outputs=output_layer)
from sklearn.model_selection import train_test_split

In [7]:
data = pd.concat([class0[:min(count)-1],class1[:min(count)-1],class2[:min(count)-1]])
names = data['Filename'].unique()


In [9]:
for name in names:
 dataN = data[data['Filename']==name]
 file = 'person/' + name+'.h5'
 X_train, X_test, y_train, y_test = train_test_split(dataN['Data_2'], dataN['Class_label'], test_size=0.33, random_state=42)
 y_test = np.array(y_test)
 y_train = np.array(y_train)
 X_train=list(X_train)
 X_test=list(X_test)
 def convX(X):
    for i in range(len(X)):
     X[i]=list(eval(X[i]))
    return np.array(X)
 x_train = convX(X_train)
 x_test=convX(X_test)
 xx = []
 for i in x_test:
    xx.append(len(i))
 print(set(xx))
 x_train = x_train.reshape((x_train.shape[0], x_train.shape[1], 1))
 x_test = x_test.reshape((x_test.shape[0], x_test.shape[1], 1))
 num_classes = len(np.unique(y_train))
 print(num_classes)
 idx = np.random.permutation(len(x_train))
 x_train = x_train[idx]
 y_train = y_train[idx]
 y_train[y_train == -1] = 0
 y_test[y_test == -1] = 0
 model = make_model(input_shape=x_train.shape[1:])
 keras.utils.plot_model(model, show_shapes=True)
 epochs = 500
 batch_size = 32

 callbacks = [
    keras.callbacks.ModelCheckpoint(
        file, save_best_only=True, monitor="val_loss"
    ),
    keras.callbacks.ReduceLROnPlateau(
        monitor="val_loss", factor=0.5, patience=20, min_lr=0.0001
    ),
    keras.callbacks.EarlyStopping(monitor="val_loss", patience=50, verbose=1),
 ]
 model.compile(
    optimizer="adam",
    loss="sparse_categorical_crossentropy",
    metrics=["sparse_categorical_accuracy"],
 )
 history = model.fit(
    x_train,
    y_train,
    batch_size=batch_size,
    epochs=epochs,
    callbacks=callbacks,
    validation_split=0.2,
    verbose=1,
 )
 model = keras.models.load_model(file)

 test_loss, test_acc = model.evaluate(x_test, y_test)

 print("Test accuracy", test_acc)
 print("Test loss", test_loss)

{240}
3
You must install pydot (`pip install pydot`) and install graphviz (see instructions at https://graphviz.gitlab.io/download/) for plot_model/model_to_dot to work.
Epoch 1/500
1/1 [==============================] - 1s 1s/step - loss: 1.2208 - sparse_categorical_accuracy: 0.2308 - val_loss: 1.7203 - val_sparse_categorical_accuracy: 0.7143 - lr: 0.0010
Epoch 2/500
1/1 [==============================] - 0s 37ms/step - loss: 0.9971 - sparse_categorical_accuracy: 0.4615 - val_loss: 2.3462 - val_sparse_categorical_accuracy: 0.7143 - lr: 0.0010
Epoch 3/500
1/1 [==============================] - 0s 33ms/step - loss: 0.9246 - sparse_categorical_accuracy: 0.5385 - val_loss: 2.8887 - val_sparse_categorical_accuracy: 0.7143 - lr: 0.0010
Epoch 4/500
1/1 [==============================] - 0s 34ms/step - loss: 0.8898 - sparse_categorical_accuracy: 0.5385 - val_loss: 3.2783 - val_sparse_categorical_accuracy: 0.7143 - lr: 0.0010
Epoch 5/500
1/1 [==============================] - 0s 34ms/step - lo

1/1 [==============================] - 0s 33ms/step - loss: 0.5879 - sparse_categorical_accuracy: 0.6923 - val_loss: 2.6754 - val_sparse_categorical_accuracy: 0.7143 - lr: 2.5000e-04
Epoch 43/500
1/1 [==============================] - 0s 33ms/step - loss: 0.5863 - sparse_categorical_accuracy: 0.7308 - val_loss: 2.6265 - val_sparse_categorical_accuracy: 0.7143 - lr: 2.5000e-04
Epoch 44/500
1/1 [==============================] - 0s 34ms/step - loss: 0.5846 - sparse_categorical_accuracy: 0.7308 - val_loss: 2.5811 - val_sparse_categorical_accuracy: 0.7143 - lr: 2.5000e-04
Epoch 45/500
1/1 [==============================] - 0s 33ms/step - loss: 0.5829 - sparse_categorical_accuracy: 0.7308 - val_loss: 2.5378 - val_sparse_categorical_accuracy: 0.7143 - lr: 2.5000e-04
Epoch 46/500
1/1 [==============================] - 0s 34ms/step - loss: 0.5811 - sparse_categorical_accuracy: 0.7308 - val_loss: 2.4954 - val_sparse_categorical_accuracy: 0.7143 - lr: 2.5000e-04
Epoch 47/500
1/1 [===============

Epoch 32/500
1/1 [==============================] - 0s 72ms/step - loss: 0.7199 - sparse_categorical_accuracy: 0.8077 - val_loss: 2.8903 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 33/500
1/1 [==============================] - 0s 69ms/step - loss: 0.7149 - sparse_categorical_accuracy: 0.8077 - val_loss: 2.8063 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 34/500
1/1 [==============================] - 0s 70ms/step - loss: 0.7099 - sparse_categorical_accuracy: 0.8077 - val_loss: 2.7343 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 35/500
1/1 [==============================] - 0s 71ms/step - loss: 0.7048 - sparse_categorical_accuracy: 0.8077 - val_loss: 2.6601 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 36/500
1/1 [==============================] - 0s 69ms/step - loss: 0.6997 - sparse_categorical_accuracy: 0.8077 - val_loss: 2.5734 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 37/500
1/1 [======================

Epoch 75/500
1/1 [==============================] - 0s 34ms/step - loss: 0.4823 - sparse_categorical_accuracy: 0.9231 - val_loss: 1.5710 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 76/500
1/1 [==============================] - 0s 32ms/step - loss: 0.4778 - sparse_categorical_accuracy: 0.9231 - val_loss: 1.5379 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 77/500
1/1 [==============================] - 0s 33ms/step - loss: 0.4720 - sparse_categorical_accuracy: 0.9615 - val_loss: 1.5480 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 78/500
1/1 [==============================] - 0s 33ms/step - loss: 0.4764 - sparse_categorical_accuracy: 0.8846 - val_loss: 1.6165 - val_sparse_categorical_accuracy: 0.2857 - lr: 0.0010
Epoch 79/500
1/1 [==============================] - 0s 33ms/step - loss: 0.4824 - sparse_categorical_accuracy: 0.9231 - val_loss: 1.6826 - val_sparse_categorical_accuracy: 0.4286 - lr: 0.0010
Epoch 80/500
1/1 [======================

Epoch 1/500
1/1 [==============================] - 1s 927ms/step - loss: 1.1933 - sparse_categorical_accuracy: 0.0690 - val_loss: 2.0395 - val_sparse_categorical_accuracy: 0.5000 - lr: 0.0010
Epoch 2/500
1/1 [==============================] - 0s 39ms/step - loss: 1.0483 - sparse_categorical_accuracy: 0.4483 - val_loss: 2.6854 - val_sparse_categorical_accuracy: 0.2500 - lr: 0.0010
Epoch 3/500
1/1 [==============================] - 0s 35ms/step - loss: 0.9953 - sparse_categorical_accuracy: 0.4483 - val_loss: 3.0645 - val_sparse_categorical_accuracy: 0.2500 - lr: 0.0010
Epoch 4/500
1/1 [==============================] - 0s 36ms/step - loss: 0.9640 - sparse_categorical_accuracy: 0.5172 - val_loss: 3.3000 - val_sparse_categorical_accuracy: 0.2500 - lr: 0.0010
Epoch 5/500
1/1 [==============================] - 0s 36ms/step - loss: 0.9490 - sparse_categorical_accuracy: 0.4483 - val_loss: 3.4322 - val_sparse_categorical_accuracy: 0.2500 - lr: 0.0010
Epoch 6/500
1/1 [===========================

...

1/1 [==============================] - 0s 44ms/step - loss: 0.8176 - sparse_categorical_accuracy: 0.5312 - val_loss: 1.0541 - val_sparse_categorical_accuracy: 0.3333 - lr: 0.0010
Epoch 27/500
1/1 [==============================] - 0s 44ms/step - loss: 0.8136 - sparse_categorical_accuracy: 0.5312 - val_loss: 1.0662 - val_sparse_categorical_accuracy: 0.3333 - lr: 0.0010
Epoch 28/500
1/1 [==============================] - 0s 44ms/step - loss: 0.8095 - sparse_categorical_accuracy: 0.5625 - val_loss: 1.0702 - val_sparse_categorical_accuracy: 0.3333 - lr: 0.0010
Epoch 29/500
1/1 [==============================] - 0s 46ms/step - loss: 0.8056 - sparse_categorical_accuracy: 0.5312 - val_loss: 1.0702 - val_sparse_categorical_accuracy: 0.4444 - lr: 0.0010
Epoch 30/500
1/1 [==============================] - 0s 45ms/step - loss: 0.8017 - sparse_categorical_accuracy: 0.5312 - val_loss: 1.0705 - val_sparse_categorical_accuracy: 0.4444 - lr: 0.0010
Epoch 31/500
1/1 [==============================] - 0

1/1 [==============================] - 0s 46ms/step - loss: 0.6999 - sparse_categorical_accuracy: 0.6562 - val_loss: 1.4283 - val_sparse_categorical_accuracy: 0.2222 - lr: 2.5000e-04
Epoch 69/500
1/1 [==============================] - 0s 45ms/step - loss: 0.6985 - sparse_categorical_accuracy: 0.6562 - val_loss: 1.4225 - val_sparse_categorical_accuracy: 0.2222 - lr: 2.5000e-04
Epoch 70/500
1/1 [==============================] - 0s 45ms/step - loss: 0.6970 - sparse_categorical_accuracy: 0.6562 - val_loss: 1.4177 - val_sparse_categorical_accuracy: 0.2222 - lr: 2.5000e-04
Epoch 71/500
1/1 [==============================] - 0s 45ms/step - loss: 0.6956 - sparse_categorical_accuracy: 0.6562 - val_loss: 1.4157 - val_sparse_categorical_accuracy: 0.2222 - lr: 2.5000e-04
Epoch 72/500
1/1 [==============================] - 0s 45ms/step - loss: 0.6941 - sparse_categorical_accuracy: 0.6562 - val_loss: 1.4168 - val_sparse_categorical_accuracy: 0.2222 - lr: 2.5000e-04
Epoch 73/500
1/1 [===============

Epoch 36/500
1/1 [==============================] - 0s 41ms/step - loss: 0.4792 - sparse_categorical_accuracy: 0.8095 - val_loss: 0.2915 - val_sparse_categorical_accuracy: 0.8333 - lr: 0.0010
Epoch 37/500
1/1 [==============================] - 0s 40ms/step - loss: 0.4760 - sparse_categorical_accuracy: 0.8095 - val_loss: 0.3007 - val_sparse_categorical_accuracy: 0.8333 - lr: 0.0010
Epoch 38/500
1/1 [==============================] - 0s 40ms/step - loss: 0.4727 - sparse_categorical_accuracy: 0.8571 - val_loss: 0.3167 - val_sparse_categorical_accuracy: 0.8333 - lr: 0.0010
Epoch 39/500
1/1 [==============================] - 0s 40ms/step - loss: 0.4696 - sparse_categorical_accuracy: 0.8571 - val_loss: 0.3382 - val_sparse_categorical_accuracy: 0.8333 - lr: 0.0010
Epoch 40/500
1/1 [==============================] - 0s 41ms/step - loss: 0.4666 - sparse_categorical_accuracy: 0.8571 - val_loss: 0.3577 - val_sparse_categorical_accuracy: 0.8333 - lr: 0.0010
Epoch 41/500
1/1 [======================

1/1 [==============================] - 0s 41ms/step - loss: 0.3756 - sparse_categorical_accuracy: 0.9048 - val_loss: 0.6906 - val_sparse_categorical_accuracy: 0.5000 - lr: 2.5000e-04
Epoch 79/500
1/1 [==============================] - 0s 41ms/step - loss: 0.3744 - sparse_categorical_accuracy: 0.9048 - val_loss: 0.6862 - val_sparse_categorical_accuracy: 0.5000 - lr: 2.5000e-04
Epoch 80/500
1/1 [==============================] - 0s 42ms/step - loss: 0.3729 - sparse_categorical_accuracy: 0.9048 - val_loss: 0.6830 - val_sparse_categorical_accuracy: 0.5000 - lr: 2.5000e-04
Epoch 80: early stopping


InvalidArgumentError: Graph execution error:

Detected at node 'sparse_categorical_crossentropy/SparseSoftmaxCrossEntropyWithLogits/SparseSoftmaxCrossEntropyWithLogits' defined at (most recent call last):
    File "C:\ProgramData\Anaconda3\lib\runpy.py", line 197, in _run_module_as_main
      return _run_code(code, main_globals, None,
    File "C:\ProgramData\Anaconda3\lib\runpy.py", line 87, in _run_code
      exec(code, run_globals)
    File "C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py", line 16, in <module>
      app.launch_new_instance()
    File "C:\ProgramData\Anaconda3\lib\site-packages\traitlets\config\application.py", line 846, in launch_instance
      app.start()
    File "C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\kernelapp.py", line 677, in start
      self.io_loop.start()
    File "C:\ProgramData\Anaconda3\lib\site-packages\tornado\platform\asyncio.py", line 199, in start
      self.asyncio_loop.run_forever()
    File "C:\ProgramData\Anaconda